#  Incidence du syndrome de varicelle

In [1]:
%matplotlib inline
import matplotlib.pyplot as plt
import pandas as pd
import isoweek

Les données de l'incidence du syndrome de varicelle sont disponibles du site Web du [Réseau Sentinelles](https://www.sentiweb.fr). Nous les récupérons sous forme d'un fichier en format CSV dont chaque ligne correspond à une semaine de la période demandée. Nous téléchargeons toujours le jeu de données complet, qui commence en 1991 et se termine avec une semaine récente.

In [2]:
data_url = "http://www.sentiweb.fr/datasets/incidence-PAY-7.csv"

La première ligne du fichier CSV est un commentaire, que nous ignorons en précisant skiprows=1.

In [3]:
raw_data = pd.read_csv(data_url, skiprows=1)
raw_data

week  indicator    inc  inc_low  inc_up  inc100  inc100_low  \
0     202012          7   8210     5823   10597      12           8   
1     202011          7  10198     7568   12828      15          11   
2     202010          7   9011     6691   11331      14          10   
3     202009          7  13631    10544   16718      21          16   
4     202008          7  10424     7708   13140      16          12   
5     202007          7   8959     6574   11344      14          10   
6     202006          7   9264     6925   11603      14          10   
7     202005          7   8505     6314   10696      13          10   
8     202004          7   7991     5831   10151      12           9   
9     202003          7   5968     4100    7836       9           6   
10    202002          7   6534     4530    8538      10           7   
11    202001          7   9835     7019   12651      15          11   
12    201952          7   7941     5246   10636      12           8   
13    201951          7   5823     3675    7971       9           6   
14    201950          7   6424     4276    8572      10           7   
15    201949          7   6621     4540    8702      10           7   
16    201948          7   5542     3383    7701       8           5   
17    201947          7   7536     5058   10014      11           7   
18    201946          7   2638     1316    3960       4           2   
19    201945          7   4492     2615    6369       7           4   
20    201944          7   5728     3627    7829       9           6   
21    201943          7   4834     2751    6917       7           4   
22    201942          7   6279     3989    8569      10           7   
23    201941          7   4130     2030    6230       6           3   
24    201940          7   4211     2218    6204       6           3   
25    201939          7   3137     1310    4964       5           2   
26    201938          7   3078     1416    4740       5           2   
27    201937          7    970      162    1778       1           0   
28    201936          7   1277      263    2291       2           0   
29    201935          7    922        0    1857       1           0   
...      ...        ...    ...      ...     ...     ...         ...   
1499  199126          7  17608    11304   23912      31          20   
1500  199125          7  16169    10700   21638      28          18   
1501  199124          7  16171    10071   22271      28          17   
1502  199123          7  11947     7671   16223      21          13   
1503  199122          7  15452     9953   20951      27          17   
1504  199121          7  14903     8975   20831      26          16   
1505  199120          7  19053    12742   25364      34          23   
1506  199119          7  16739    11246   22232      29          19   
1507  199118          7  21385    13882   28888      38          25   
1508  199117          7  13462     8877   18047      24          16   
1509  199116          7  14857    10068   19646      26          18   
1510  199115          7  13975     9781   18169      25          18   
1511  199114          7  12265     7684   16846      22          14   
1512  199113          7   9567     6041   13093      17          11   
1513  199112          7  10864     7331   14397      19          13   
1514  199111          7  15574    11184   19964      27          19   
1515  199110          7  16643    11372   21914      29          20   
1516  199109          7  13741     8780   18702      24          15   
1517  199108          7  13289     8813   17765      23          15   
1518  199107          7  12337     8077   16597      22          15   
1519  199106          7  10877     7013   14741      19          12   
1520  199105          7  10442     6544   14340      18          11   
1521  199104          7   7913     4563   11263      14           8   
1522  199103          7  15387    10484   20290      27          18   
1523  199102          7  16277  

 Y a-t-il des points manquants dans ce jeux de données ? Non

In [6]:
raw_data[raw_data.isnull().any(axis=1)]
data = raw_data.copy()

Nos données utilisent une convention inhabituelle: le numéro de semaine est collé à l'année, donnant l'impression qu'il s'agit de nombre entier. C'est comme ça que Pandas les interprète.Un deuxième problème est que Pandas ne comprend pas les numéros de semaine.  Il faut lui fournir les dates de début et de fin de semaine. Nous utilisons pour cela la bibliothèque isoweek. Comme la conversion des semaines est devenu assez complexe, nous écrivons une petite fonction Python pour cela. Ensuite, nous l'appliquons à tous les points de nos donnés. Les résultats vont dans une nouvelle colonne 'period'.

In [7]:
def convert_week(year_and_week_int):
    year_and_week_str = str(year_and_week_int)
    year = int(year_and_week_str[:4])
    week = int(year_and_week_str[4:])
    w = isoweek.Week(year, week)
    return pd.Period(w.day(0), 'W')

data['period'] = [convert_week(yw) for yw in data['week']]

Il reste deux petites modifications à faire.Premièrement, nous définissons les périodes d'observation
comme nouvel index de notre jeux de données. Ceci en fait
une suite chronologique, ce qui sera pratique par la suite.Deuxièmement, nous trions les points par période, dans
le sens chronologique.